In [1]:
import pandas as pd
import numpy as np
import limix
import qtl_output
import qtl_loader_utils
from qtl_snp_qc import do_snp_qc
from bgen_reader import read_bgen
import glob
import os
from sklearn.preprocessing import Imputer
import argparse

In [2]:
#From loader utils
def ensure_dir(file_path):
    '''Check if directory exists for output, and create it if it doesn't.'''
    directory = os.path.dirname(file_path)
    if not os.path.exists(directory):
        os.makedirs(directory)

##Read snp filterlist
def get_snp_df(snps_filename):
    if snps_filename:
        snp_filter_df = pd.read_csv(snps_filename,sep='\t',index_col=0)
    else:
        snp_filter_df = None
    return snp_filter_df

def get_kinship_df(kinship_filename):
    if kinship_filename:
        kinship_df = pd.read_csv(kinship_filename,sep='\t',index_col=0)
    else:
        kinship_df = None
    return kinship_df

def get_samplemapping_df(sample_mapping_filename,sample_labels,key_from):
    assert(key_from in ['iid','sample'])
    if sample_mapping_filename:
        mapping_df = pd.read_csv(sample_mapping_filename,sep='\t',header=None,names=['iid','sample'])
        mapping_df.set_index(key_from,inplace=True)
    else:
        #assume the mapping is the identity mapping
        identifiers = sample_labels
        mapping_df = pd.DataFrame(data=np.vstack([identifiers,identifiers]).T,index=identifiers,columns=['iid','sample'])
    return mapping_df

def get_covariate_df(covariates_filename):
    if covariates_filename:
        covariate_df = pd.read_csv(covariates_filename,sep='\t',index_col=0)
    else:
        covariate_df = None
    return covariate_df

def get_genotype_data(geno_prefix):
    bim,fam,bed = limix.io.read_plink(geno_prefix,verbose=False)
    fam.set_index('iid',inplace=True)
    return bim,fam,bed

def get_annotation_df(anno_filename):
    annotation_col_dtypes = {'feature_id':np.object,
                         'gene_id':np.object,
                         'gene_name':np.object,
                         'chromosome':np.object,
                         'start':np.int64,
                         'end':np.int64,
                         'strand':np.object}
    annotation_df = pd.read_csv(anno_filename,sep='\t',index_col=0,dtype=annotation_col_dtypes)
    return annotation_df

def get_phenotype_df(pheno_filename):
    return pd.read_csv(pheno_filename,sep='\t',index_col=0)


In [3]:
#From snp_qc

def do_snp_qc(snp_df, min_call_rate, min_maf, min_hwe_P):
   
    #Determine call rate.
    call_rate = 1-snp_df.isnull().sum()/len(snp_df.index)
    selection = call_rate < min_call_rate
    #print("Pass CR: ");print(snp_df.isnull().sum())
    #print(call_rate)
    #print(call_rate < min_call_rate)
    failed_snp_names  = list(snp_df.columns[selection])
    snp_df_c = snp_df.loc[:,list(snp_df.columns[~selection])]
    #print("Pass CR: ");print(snp_df_c.shape)
    if(len(snp_df_c.columns)==0):
        return snp_df_c.columns, failed_snp_names
    #Determine MAF.
    genotypeCounter = np.zeros((len(snp_df_c.columns),3), dtype=np.int)
    for allele_index in [0,1,2]:
        genotypeCounter[:,allele_index] = np.nansum(np.around(snp_df_c.values)==allele_index,0)

    #Here we make sure that the major allele is temporarly 'coded' as 0 & directly calculate the MAF (based on allele counts and non NA samples)
    
    mac = np.zeros((len(snp_df_c.columns)), dtype=np.int)
    gc = np.zeros((len(snp_df_c.columns)), dtype=np.int)
    maf = np.zeros((len(snp_df_c.columns)), dtype=np.float)

    for snp in range(0, len(snp_df_c.columns)):
        if genotypeCounter[snp,0]<genotypeCounter[snp,2]:
            tmp = genotypeCounter[snp,0]
            genotypeCounter[snp,0] = genotypeCounter[snp,2]
            genotypeCounter[snp,2] = tmp
        mac[snp] = int((genotypeCounter[snp,2]*2)+genotypeCounter[snp,1])
        gc[snp] = int(genotypeCounter[snp,2]+genotypeCounter[snp,1]+genotypeCounter[snp,0])
        maf[snp] = mac[snp] / (float(2*gc[snp]))
    
    selection = maf < min_maf
    failed_snp_names.extend(list(snp_df_c.columns[selection]))
    snp_df_c = snp_df_c.iloc[:,~selection]
    #print("Pass MAF: ");print(snp_df_c.shape)
    if(len(snp_df_c.columns)==0):
        return snp_df_c.columns, failed_snp_names
    
    mac=mac[~selection]
    gc=gc[~selection]
    genotypeCounter = genotypeCounter[~selection,]
    
    #Determine HWE.
    hweP = np.zeros((len(snp_df_c.columns)), dtype=np.float)
    #print(len(snp_df_c.columns))
    #print(len(mac))
    #This can also be multi-threaded if we place it in an separate function. (And multi-threading is as easy as it seems)
    for snp in range(0, len(snp_df_c.columns)):
        rare_copies = mac[snp]
        genotypes = gc[snp]
        
        
        het_probs = np.zeros((rare_copies+1))
        # start at midpoint #

        mid = int(math.floor(rare_copies * (2 * genotypes - rare_copies) / (2 * genotypes)))

        # check to ensure that midpoint and rare alleles have same parity #
        if int(mid % 2) != int(rare_copies % 2) :
            mid+=1
        
        curr_homr = int(math.floor((rare_copies - mid) / 2))
        curr_homc = genotypes - mid - curr_homr

        #print(het_probs.shape)
        het_probs[mid] = 1.0
        sum_values = het_probs[mid]
        for curr_hets in range(mid, 0, -2) :
            het_probs[curr_hets - 2] = het_probs[curr_hets] * curr_hets * (curr_hets - 1.0) / (4.0 * (curr_homr + 1.0) * (curr_homc + 1.0))
            sum_values += het_probs[curr_hets - 2]
            ## 2 fewer heterozygotes for next iteration -> add one rare, one common homozygote ##
            curr_homr+=1
            curr_homc+=1

        curr_homr = int(math.floor((rare_copies - mid) / 2))
        curr_homc = genotypes - mid - curr_homr

        for curr_hets in range(mid, (rare_copies), 2) :
            het_probs[curr_hets + 2] = het_probs[curr_hets] * 4.0 * curr_homr * curr_homc / ((curr_hets + 2.0) * (curr_hets + 1.0))
            sum_values += het_probs[curr_hets + 2]
            curr_homr-=1
            curr_homc-=1
        
        p_hwe = 0.0
        het_probs[int(genotypeCounter[snp,1])]/= sum_values
        for index in range(0,rare_copies+1) :
            if index != int(genotypeCounter[snp,1]) :
                het_probs[index] /= sum_values
            if het_probs[index] <= het_probs[int(genotypeCounter[snp,1])] :
                p_hwe += het_probs[index];

        hweP[snp] = 1 if p_hwe > 1.0 else p_hwe;
    selection = hweP < min_hwe_P
    failed_snp_names.extend(list(snp_df_c.columns[selection]))
    snp_df_c = snp_df_c.loc[:,list(snp_df_c.columns[~selection])]
    #print("Pass HWE: ");print(snp_df_c.shape)
    return snp_df_c.columns, failed_snp_names

def do_snp_qc_stringent(snp_df, min_call_rate, min_maf, min_hwe_P, min_hmachR2):
   
    #Determine call rate.
    call_rate = 1-snp_df.isnull().sum()/len(snp_df.index)
    selection = call_rate < min_call_rate
    #print(call_rate)
    #print(call_rate < min_call_rate)
    failed_snp_names  = list(snp_df.columns[selection])
    snp_df_c = snp_df.loc[:,list(snp_df.columns[~selection])]
    if(len(snp_df_c.columns)==0):
        return snp_df_c.columns, failed_snp_names
    #Determine MAF.
    genotypeCounter = np.zeros((len(snp_df_c.columns),3), dtype=np.int)
    for allele_index in [0,1,2]:
        genotypeCounter[:,allele_index] = np.nansum(np.around(snp_df_c.values)==allele_index,0)

    #Here we make sure that the major allele is temporarly 'coded' as 0 & directly calculate the MAF (based on allele counts and non NA samples)
    mac = np.zeros((len(snp_df_c.columns)), dtype=np.int)
    gc = np.zeros((len(snp_df_c.columns)), dtype=np.int)
    maf = np.zeros((len(snp_df_c.columns)), dtype=np.float)
    for snp in range(0, len(snp_df_c.columns)):
        if genotypeCounter[snp,0]<genotypeCounter[snp,2]:
            tmp = genotypeCounter[snp,0]
            genotypeCounter[snp,0] = genotypeCounter[snp,2]
            genotypeCounter[snp,2] = tmp
        mac[snp] = int((genotypeCounter[snp,2]*2)+genotypeCounter[snp,1])
        gc[snp] = int(genotypeCounter[snp,2]+genotypeCounter[snp,1]+genotypeCounter[snp,0])
        maf[snp] = mac[snp] / (float(2*gc[snp]))
    
    selection = maf < min_maf
    
    failed_snp_names.extend(list(snp_df_c.columns[selection]))
    snp_df_c = snp_df_c.loc[:,list(snp_df_c.columns[~selection])]
    
    if(len(snp_df_c.columns)==0):
        return snp_df_c.columns, failed_snp_names
    
    mac=mac[~selection]
    gc=gc[~selection]
    genotypeCounter = genotypeCounter[~selection,]
    
    #Determine HWE.
    hweP = np.zeros((len(snp_df_c.columns)), dtype=np.float)
    
    for snp in range(0, len(snp_df_c.columns)):
        rare_copies = mac[snp]
        genotypes = gc[snp]
        
        
        het_probs = np.zeros((rare_copies+1))
        # start at midpoint #

        mid = int(math.floor(rare_copies * (2 * genotypes - rare_copies) / (2 * genotypes)))

        # check to ensure that midpoint and rare alleles have same parity #
        if int(mid % 2) != int(rare_copies % 2) :
            mid+=1
        
        curr_homr = int(math.floor((rare_copies - mid) / 2))
        curr_homc = genotypes - mid - curr_homr

        #print(het_probs.shape)
        het_probs[mid] = 1.0
        sum_values = het_probs[mid]
        for curr_hets in range(mid, 0, -2) :
            het_probs[curr_hets - 2] = het_probs[curr_hets] * curr_hets * (curr_hets - 1.0) / (4.0 * (curr_homr + 1.0) * (curr_homc + 1.0))
            sum_values += het_probs[curr_hets - 2]
            ## 2 fewer heterozygotes for next iteration -> add one rare, one common homozygote ##
            curr_homr+=1
            curr_homc+=1

        curr_homr = int(math.floor((rare_copies - mid) / 2))
        curr_homc = genotypes - mid - curr_homr

        for curr_hets in range(mid, (rare_copies), 2) :
            het_probs[curr_hets + 2] = het_probs[curr_hets] * 4.0 * curr_homr * curr_homc / ((curr_hets + 2.0) * (curr_hets + 1.0))
            sum_values += het_probs[curr_hets + 2]
            curr_homr-=1
            curr_homc-=1
        
        p_hwe = 0.0
        het_probs[int(genotypeCounter[snp,1])]/= sum_values
        for index in range(0,rare_copies+1) :
            if index != int(genotypeCounter[snp,1]) :
                het_probs[index] /= sum_values
            if het_probs[index] <= het_probs[int(genotypeCounter[snp,1])] :
                p_hwe += het_probs[index];

        hweP[snp] = 1 if p_hwe > 1.0 else p_hwe;
    selection = hweP < min_hwe_P
    failed_snp_names.extend(list(snp_df_c.columns[selection]))
    snp_df_c = snp_df_c.loc[:,list(snp_df_c.columns[~selection])]
    
    if(len(snp_df_c.columns)==0):
        return snp_df_c.columns, failed_snp_names
    
    gc = gc[~selection]
    genotypeCounter = genotypeCounter[~selection,]
    
    machR2 = np.zeros((len(snp_df_c.columns)), dtype=np.float)
    for snp in range(0, len(snp_df_c.columns)):
        dosageSum = 0.0
        dosageSqrSum = 0.0
        dosageSum += genotypeCounter[snp,1]
        dosageSum += genotypeCounter[snp,2]*2
        dosageSqrSum += math.pow(1, 2)*genotypeCounter[snp,1]
        dosageSqrSum += math.pow(2, 2)*genotypeCounter[snp,2]
        nonMissingCount = gc[snp]
        estimatedAlleleFrequency = dosageSum / (2 * nonMissingCount)
        if (estimatedAlleleFrequency <= 0 or estimatedAlleleFrequency >= 1) :
            machR2[snp] = 1
        tmpR2 = ((dosageSqrSum / nonMissingCount) - math.pow((dosageSum / nonMissingCount), 2)) / (2 * estimatedAlleleFrequency * (1 - estimatedAlleleFrequency))
        machR2[snp] = 1 if tmpR2 > 1.0 else tmpR2
    selection = machR2 < min_hmachR2
    
    failed_snp_names.extend(list(snp_df_c.columns[selection]))
    snp_df_c = snp_df_c.loc[:,list(snp_df_c.columns[~selection])]
    
    return snp_df_c.columns, failed_snp_names

In [4]:
#From QTL utils 

def merge_QTL_results(results_dir):
    '''Merge QTL results for individual chromosomes into a combined, indexed
    hdf5 file.'''
    qtl_results_files = sorted(glob.glob(results_dir+'qtl_results_*.txt'))

    hdf5_outfile = qtl_output.hdf5_writer(results_dir+'qtl_results.h5')

    for filename in qtl_results_files:
        df = pd.read_csv(filename,sep='\t')
        hdf5_outfile.add_result_df(df)

    hdf5_outfile.close()
        

def chunker(seq, size):
    return (seq[pos:pos + size] for pos in range(0, len(seq), size))

def get_unique_genetic_samples(kinship_df, relatedness_score):
#    tril returns the lower triungular.
#    if two lines are > identity then  kinship_df>=relatedness_score should have an offdiagonal 1.
#    if there is one 1  in the tril then it means that  in the upper triul there was a line withe identical genotype
    return (kinship_df.index[(np.tril(kinship_df>=relatedness_score,k=-1)).sum(1)==0])

def force_normal_distribution(phenotype, method='gaussnorm', reference=None):
    _doc='rank transform x into ref/ gaussian;keep the range; keep ties'

    if method=='log':
        return np.log(1+phenotype)

    indextoupdate=np.isfinite(phenotype);
    y1=phenotype[indextoupdate]
    yuni,yindex=np.unique(y1, return_inverse=True)

    if method=='gaussnorm':
        std=np.nanstd(y1)
        mean=np.nanmedian(y1)
#        sref = scst.norm.isf(np.linspace(max(0.0001,scst.norm.cdf((np.nanmin(y1)-mean)/std)), min(0.9999,scst.norm.cdf((np.nanmax(y1)-mean)/std)),num=yuni.shape[0])[::-1])
        sref = scst.norm.isf(np.linspace(0.001, 0.999,num=yuni.shape[0])[::-1])

    elif method=='ranknorm':
        try:
            sref=np.sort(reference[np.isfinite(reference)])[np.linspace(0,reference.shape[0]-0.001, num=yuni.shape[0]).astype(int)]
        except: print ('reference missing. provide reference to force_normal_distribution or choose gaussnorm')
    phenotypenorm=phenotype.copy()
    phenotypenorm[indextoupdate]=sref[yindex]

    return phenotypenorm

#get_shuffeld_genotypes_preserving_kinship(geneticaly_unique_individuals, relatedness_score, snp_matrix_DF,kinship_df.loc[individual_ids,individual_ids], n_perm)
def get_shuffeld_genotypes_preserving_kinship(geneticaly_unique_individuals, relatedness_score, snp_matrix_DF,kinship_df1,n_perm):

#    snp_matrix_DF.iloc[np.unique(snp_matrix_DF.index,return_index=1)[1]].shape
    '''take only one line for replicates (those with the same name)'''
    temp=snp_matrix_DF.iloc[np.unique(snp_matrix_DF.index,return_index=1)[1]].copy(deep=True)
    u_snp_matrix = temp.loc[geneticaly_unique_individuals,:]
    kinship_df1=kinship_df1.iloc[np.unique(kinship_df1.index,return_index=1)[1],np.unique(kinship_df1.index,return_index=1)[1]]
    '''has replicates but not same lines form donor (np.setdiff1d(individual_ids,geneticaly_unique_individuals))'''
    #Shuffle and reinflate
    locationBuffer = np.zeros(snp_matrix_DF.shape[0], dtype=np.int)
    #Prepare location search for permuted snp_matrix_df.
    index = 0
    index_samples = np.arange(u_snp_matrix.shape[0])
    for current_name in geneticaly_unique_individuals :
        selection = kinship_df1.loc[current_name].values>=relatedness_score
        locationBuffer[np.where(selection)] = index
        index +=1
    snp_matrix_copy = np.zeros((snp_matrix_DF.shape[0],snp_matrix_DF.shape[1]*n_perm))
    counter = 0
    end = (snp_matrix_DF.shape[1])
    for perm_id in range(0,n_perm) :
        np.random.shuffle(index_samples)
        temp_u = u_snp_matrix.values[index_samples,:]
        snp_matrix_copy[:,counter:end] = temp_u[locationBuffer,:]
        counter+= snp_matrix_DF.shape[1]
        end+= snp_matrix_DF.shape[1]
    return(snp_matrix_copy)

def get_shuffeld_genotypes(snp_matrix_DF,kinship_df,n_perm):
    snp_matrix_copy = np.zeros((snp_matrix_DF.shape[0],snp_matrix_DF.shape[1]*n_perm))
    counter = 0
    end = (snp_matrix_DF.shape[1])

    index_samples = np.arange(snp_matrix_DF.shape[0])
    for perm_id in range(0,n_perm) :
        np.random.shuffle(index_samples)
        snp_matrix_copy[:,counter:end] = snp_matrix_DF.values[index_samples,:]
        counter+= snp_matrix_DF.shape[1]
        end+= snp_matrix_DF.shape[1]
    return(snp_matrix_copy)

def qtl_plot(snp_matrix_DF, phenotype,K=None, M=None,LMM=None,snp=None,show_reg_cov=True):
    if LMM is None:
        LMM = limix.qtl.qtl_test_lmm(snp_matrix_DF.values, phenotype,K=K,M=M,verbose=False)
        
    if snp is None:
        snp=snp_matrix_DF.values[:,np.argmin(LMM.variant_effsizes)]           
    
    cov=LMM.null_covariate_effsizes;betacov=np.array([cov[key] for key in cov.keys()])


    temp=pd.DataFrame(data=np.hstack([np.vstack([snp,phenotype,np.zeros(phenotype.shape[0]).astype(bool)]),\
                                          np.vstack([snp,phenotype-np.dot(M,betacov[:,None])[:,0],np.ones(phenotype.shape[0]).astype(bool)])]).T,\
                                            columns=['Variant','Phenotype donor','Covariates regressed'])
    
    temp['Covariates regressed']=temp['Covariates regressed'].astype(bool)
 
    indexunique=np.unique(np.array([l.split('-')[1] for l in snp_matrix_DF.index]),return_index=1)[1]
    ax = sb.boxplot(y=temp['Phenotype donor'],x=temp['Variant'])
    for patch in ax.artists:
        r, g, b, a = patch.get_facecolor()
        patch.set_facecolor((r, g, b, .03))
 
#    sb.swarmplot(y=temp['Phenotype donor'],x=temp['Variant'],color='grey')
    if show_reg_cov:
        index1=np.hstack([indexunique,indexunique+phenotype.shape[0]])
        sb.swarmplot(y=temp['Phenotype donor'].iloc[index1],x=temp['Variant'].iloc[index1],  hue=temp['Covariates regressed'].iloc[index1], split=True)
    else:
        index1= indexunique 
        sb.swarmplot(y=temp['Phenotype donor'].iloc[index1],x=temp['Variant'].iloc[index1])

In [40]:
#settings
pheno_filename = '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Expression/Geuvadis_CEU_YRI_Expr.txt.gz'
anno_filename = '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Expression/Geuvadis_CEU_Annot_small2.txt'
#geno_prefix = '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Genotypes/1000gCeuChr20Mb6'
geno_prefix = '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Genotypes/Geuvadis'
plinkGenotype=False
#plinkGenotype=True


window_size = 250000
min_maf = 0.05
min_hwe_P = 0.01
min_call_rate = 0.95
cis_mode = True
# cis_mode = False
n_perm=10000
minimum_test_samples = 10
relatedness_score = 0.95
output_dir = '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/outputTest'
#chromosome='all'
#chromosome='1'
chromosome='1:0-1000000'
feature_filename = None
snps_filename = None
write_permutations = False

covariates_filename='/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Expression/Geuvadis_CEU_YRI_covariates.txt'
kinship_filename='/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Genotypes/Geuvadis_chr1_kinship.normalized.txt'
sample_mapping_filename='/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Geuvadis_CEU_gte.txt'


In [41]:
#need to take over!
start = None
stop = None
print(chromosome)
if(":" in chromosome):
    parts = chromosome.split(":")
    if("-" not in parts[1]):
        print("No correct sub selection.")
        print("Given in: "+chromosome)
        print("Expected format: (chr number):(start location)-(stop location)")
        sys.exit()
    
    chromosome = parts[0]
    if("-" in parts[1]):
        parts2 = parts[1].split("-") 
        start = parts2[0]
        stop = parts2[1]
    print(parts[0]+"\t"+start+"\t"+stop)

1:0-1000000
1	0	1000000


In [42]:
def run_QTL_analysis_load_intersect_phenotype_covariates_kinxhip_sample_mapping\
        (pheno_filename, anno_filename, geno_prefix, plinkGenotype,minimum_test_samples= 10, relatedness_score=0.95,cis_mode=True, snps_filename=None,
         feature_filename=None, chromosome='all',  covariates_filename=None, kinship_filename=None, sample_mapping_filename=None):
 

    ''' function to take input and intersect sample and genotype.'''
    #Load input data files & filter for relevant data
    #Load input data filesf

    print(geno_prefix)

    if(plinkGenotype):
        bim,fam,bed = qtl_loader_utils.get_genotype_data(geno_prefix)
        bgen=None
        print(bim.head())
        print(fam.head())

    else :
        bgen = read_bgen(geno_prefix+'.bgen', verbose=False)
        bim = bgen['variants']
        bim = bim.assign(i = range(bim.shape[0]))
        bim = bim.rename(index=str, columns={"id": "snp"})
        #Here we need to get
        fam = bgen['samples']
        fam = fam.rename(index=str, columns={"id": "iid"})
        fam.index=fam["iid"]
        bed=None
    #     print(bim.head())
    #     print(fam.head())
    #     print(bgen['genotype'][1].compute())


    print("Intersecting data.")
    phenotype_df = qtl_loader_utils.get_phenotype_df(pheno_filename)
    annotation_df = qtl_loader_utils.get_annotation_df(anno_filename)

    sample2individual_df = qtl_loader_utils.get_samplemapping_df(sample_mapping_filename,list(phenotype_df.columns),'sample')
    sample2individual_df['sample']=sample2individual_df.index

    ##Filter first the linking files!
    #Subset linking to relevant genotypes.
    orgSize = sample2individual_df.shape[0]
    sample2individual_df = sample2individual_df.loc[sample2individual_df['iid'].map(lambda x: x in list(map(str, fam.index))),:]
    diff = orgSize- sample2individual_df.shape[0]
    orgSize = sample2individual_df.shape[0]
    print("Dropped: "+str(diff)+" samples becuase they are not present in the genotype file.")

    #Subset linking to relevant phenotypes.
    sample2individual_df = sample2individual_df.loc[np.intersect1d(sample2individual_df.index,phenotype_df.columns),:]
    diff = orgSize- sample2individual_df.shape[0]
    orgSize = sample2individual_df.shape[0]
    print("Dropped: "+str(diff)+" samples becuase they are not present in the phenotype file.")
    #Subset linking vs kinship.
    kinship_df = qtl_loader_utils.get_kinship_df(kinship_filename)
    if kinship_df is not None:
        #Filter from individual2sample_df & sample2individual_df since we don't want to filter from the genotypes.
        sample2individual_df = sample2individual_df[sample2individual_df['iid'].map(lambda x: x in list(map(str, kinship_df.index)))]
        diff = orgSize- sample2individual_df.shape[0]
        orgSize = sample2individual_df.shape[0]
        print("Dropped: "+str(diff)+" samples becuase they are not present in the kinship file.")
    #Subset linking vs covariates.
    covariate_df = qtl_loader_utils.get_covariate_df(covariates_filename)
    if covariate_df is not None:
        if np.nansum(covariate_df==1,0).max()<covariate_df.shape[0]: covariate_df.insert(0, 'ones',np.ones(covariate_df.shape[0]))
        sample2individual_df = sample2individual_df.loc[list(set(sample2individual_df.index) & set(covariate_df.index)),:]
        diff = orgSize- sample2individual_df.shape[0]
        orgSize = sample2individual_df.shape[0]
        print("Dropped: "+str(diff)+" samples becuase they are not present in the kinship file.")

    ###
    print("Number of samples with genotype & phenotype data: " + str(sample2individual_df.shape[0]))
    if(sample2individual_df.shape[0]<minimum_test_samples):
        print("Not enough samples with both genotype & phenotype data.")
        sys.exit()

    ##Filter now the actual data!
    #Filter phenotype data based on the linking files.
    phenotype_df = phenotype_df.loc[list(set(phenotype_df.index)&set(annotation_df.index)),sample2individual_df.index.values]

    #Filter kinship data based on the linking files.
    geneticaly_unique_individuals = None
    if kinship_df is not None:
        kinship_df = kinship_df.loc[np.intersect1d(kinship_df.index,sample2individual_df['iid']),np.intersect1d(kinship_df.index,sample2individual_df['iid'])]
        geneticaly_unique_individuals = get_unique_genetic_samples(kinship_df, relatedness_score);

    #Filter covariate data based on the linking files.
    if covariate_df is not None:
        covariate_df = covariate_df.loc[sample2individual_df.index,:]
        minimum_test_samples += covariate_df.shape[1]
    try:
        feature_filter_df = qtl_loader_utils.get_snp_df(feature_filename)
    except:
        if feature_filename  is not None:
            feature_filter_df=pd.DataFrame(index=feature_filename)
    #Do filtering on features.
    if feature_filter_df is not None:
        phenotype_df = phenotype_df.loc[feature_filter_df.index,:]
        ##Filtering on features and SNPs to test.

    #Prepare to filter on snps.
    snp_filter_df = qtl_loader_utils.get_snp_df(snps_filename)
    if snps_filename is not None:
        bim=bim[np.in1d(bim['snp'],snp_filter_df.index)]

    #Remove features from the annotation that are on chromosomes which are not present anyway.
    annotation_df = annotation_df = annotation_df[np.in1d(annotation_df['chromosome'],list(set(bim['chrom'])))]
    #Filtering for sites on non allosomes.
    annotation_df = annotation_df[annotation_df['chromosome'].map(lambda x: x in list(map(str, range(1, 23))))]

        #Determine features to be tested
    if chromosome=='all':
        feature_list = list(set(annotation_df.index)&set(phenotype_df.index))
    else:
        feature_list = list(set(annotation_df[annotation_df['chromosome']==chromosome].index)&set(phenotype_df.index))

    if ((not cis_mode) and len(set(bim['chrom']))<22) :
        print("Warning, running a trans-analysis on snp data from less than 22 chromosomes.\nTo merge data later the permutation P-values need to be written out.")
    print("Number of features to be tested: " + str(phenotype_df.shape[0]))

    if(phenotype_df.shape[1]<minimum_test_samples):
        print("Not enough samples with both genotype & phenotype data, for current number of covariates.")
        sys.exit()
    return [phenotype_df, kinship_df, covariate_df, sample2individual_df,annotation_df,snp_filter_df, geneticaly_unique_individuals, minimum_test_samples, feature_list,bim,fam,bed,bgen]


In [43]:
[phenotype_df, kinship_df, covariate_df, sample2individual_df,annotation_df,snp_filter_df, geneticaly_unique_individuals, minimum_test_samples, feature_list,bim,fam,bed,bgen]=\
run_QTL_analysis_load_intersect_phenotype_covariates_kinxhip_sample_mapping(pheno_filename=pheno_filename, anno_filename=anno_filename, geno_prefix=geno_prefix, plinkGenotype=plinkGenotype, cis_mode=cis_mode,
                  minimum_test_samples= minimum_test_samples,  relatedness_score=relatedness_score, snps_filename=snps_filename, feature_filename=feature_filename, chromosome=chromosome,
                 covariates_filename=covariates_filename, kinship_filename=kinship_filename, sample_mapping_filename=sample_mapping_filename)

#Open output files

# qtl_loader_utils.ensure_dir(output_dir)
if not start is None :
    output_writer = qtl_output.hdf5_writer(output_dir+'qtl_results_{}_{}_{}.h5'.format(chromosome,start,stop))
else :
    output_writer = qtl_output.hdf5_writer(output_dir+'qtl_results_{}.h5'.format(chromosome))
if(write_permutations):
    permutation_writer = qtl_output.hdf5_permutations_writer(output_dir+'perm_results_{}.h5'.format(chromosome),n_perm)

/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Genotypes/Geuvadis
Reading variants (it should take less than a minute)... done.
Intersecting data.
Dropped: 0 samples becuase they are not present in the genotype file.
Dropped: 0 samples becuase they are not present in the phenotype file.
Dropped: 0 samples becuase they are not present in the kinship file.
Dropped: 0 samples becuase they are not present in the kinship file.
Number of samples with genotype & phenotype data: 90
Number of features to be tested: 10


ValueError: The file '/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/outputTestqtl_results_1_0_1000000.h5' is already opened.  Please close it before reopening in write mode.

In [44]:
# Core function to take input and run QTL tests on a given chromosome.
#Load input data files & filter for relevant data
phenotype_df = qtl_loader_utils.get_phenotype_df(pheno_filename)
individual2sample_df = qtl_loader_utils.get_samplemapping_df(sample_mapping_filename,list(phenotype_df.columns),'iid')
sample2individual_df = qtl_loader_utils.get_samplemapping_df(sample_mapping_filename,list(phenotype_df.columns),'sample')
annotation_df = qtl_loader_utils.get_annotation_df(anno_filename)
if(plinkGenotype):
    bim,fam,bed = qtl_loader_utils.get_genotype_data(geno_prefix)
    phenotype_df = phenotype_df.loc[annotation_df.index.values,individual2sample_df.loc[list(set(fam.index)&set(individual2sample_df.index)),'sample'].values]
    kinship_df = qtl_loader_utils.get_kinship_df(kinship_filename)    
    kinship_df = kinship_df.loc[list(set(fam.index)&set(individual2sample_df.index)),list(set(fam.index)&set(individual2sample_df.index))]

    covariate_df = qtl_loader_utils.get_covariate_df(covariates_filename)
    covariate_df = covariate_df.loc[individual2sample_df.loc[list(set(fam.index)&set(individual2sample_df.index)),'sample'].values,]

else :
    print(geno_prefix)
    bgen = read_bgen(geno_prefix+'.bgen', verbose=False)
    bgen_var = bgen['variants']
    #Here we need to get
    bgen_samples = bgen['samples']
    
    phenotype_df = phenotype_df.loc[annotation_df.index.values,individual2sample_df.loc[list(set(bgen_samples)&set(individual2sample_df.index)),'sample'].values]
    kinship_df = qtl_loader_utils.get_kinship_df(kinship_filename)    
    kinship_df = kinship_df.loc[list(set(bgen_samples)&set(individual2sample_df.index)),list(set(bgen_samples)&set(individual2sample_df.index))]

    covariate_df = qtl_loader_utils.get_covariate_df(covariates_filename)
    covariate_df = covariate_df.loc[individual2sample_df.loc[list(set(bgen_samples)&set(individual2sample_df.index)),'sample'].values,]
    print(bgen['variants'].head())
    print(bgen['samples'].head())
#     print(len(bgen['genotype']))
#     print(bgen['genotype'][0].compute())


print(covariate_df.shape)

### make sure covariates, kinship & phenotype is not changed in a later stage.

/hps/nobackup/stegle/users/mjbonder/tools/hipsci_pipeline/limix_QTL_pipeline/geuvadis_CEU_test_data/Genotypes/Geuvadis
Reading variants (it should take less than a minute)... done.
  allele_ids chrom            id  nalleles     pos          rsid
0        G,C     1   snp_1_79772         2   79772   snp_1_79772
1        G,T     1   snp_1_82676         2   82676   snp_1_82676
2        G,A     1  snp_1_135032         2  135032  snp_1_135032
3        A,G     1  snp_1_172595         2  172595  snp_1_172595
4        C,T     1  snp_1_534198         2  534198  snp_1_534198
        id
0  NA06985
1  NA07346
2  NA11832
3  NA11840
4  NA11881
(0, 5)


In [49]:
print(annotation_df)
len(annotation_df.index)
#annotation_df.index.unique.values
if(annotation_df.shape[0] != annotation_df.drop_duplicates().shape[0]): 
    print("Error")
print(annotation_df.groupby(annotation_df.index).first().shape[0])


                chromosome    start      end
feature_id                                  
ENSG00000225630          1   565020   566063
ENSG00000230415          1  1210603  1215800
ENSG00000227950          1  6894393  6894678
ENSG00000049239          1  9294834  9331396
ENSG00000204859          1  6640061  6649340
ENSG00000237330          1  1007126  1009687
ENSG00000131591          1  1017198  1051741
ENSG00000171621          1  9352939  9429591
ENSG00000171612          1  9599541  9642831
ENSG00000188807          1  9648932  9674935
ENSG00000188807          1  9648934  9674935
ENSG00000188807          1  9648932  9674935
Error
10


In [34]:

if(cis_mode):
    #Remove features from the annotation that are on chromosomes which are not present anyway.
    if(plinkGenotype):
        annotation_df = annotation_df = annotation_df[np.in1d(annotation_df['chromosome'],list(set(bim['chrom'])))]
    else: 
        print(bgen_var['chrom'].lstrip(0))
        print(annotation_df['chromosome'])
        annotation_df = annotation_df = annotation_df[np.in1d(annotation_df['chromosome'],list(set(bgen_var['chrom'].lstrip(0))))]
    annotation_df = annotation_df[annotation_df['chromosome'].map(lambda x: x in list(map(str, range(1, 23))))]

#Determine features to be tested
if chromosome=='all':
    feature_list = list(set(annotation_df.index)&set(phenotype_df.index))    
else:
    feature_list = list(set(annotation_df[annotation_df['chromosome']==chromosome].index)&set(phenotype_df.index))

print(annotation_df)
# #Array to store indices of snps tested
# tested_snp_idxs = []

# feature_id = feature_list[1]
# print(feature_id)

AttributeError: 'Series' object has no attribute 'lstrip'

In [26]:
#print(annotation_df)
#(annotation_df["start"]>=9879532) & (annotation_df["end"]<=9886287)
annotation_df.iloc[(annotation_df["start"].values>=9879532) & (annotation_df["end"].values<=9886287)].index.values
#feature_list = list(set(annotation_df[(annotation_df["start"]>=9879532) & (annotation_df["end"]<=9886287)].index)&set(phenotype_df.index))

array(['ENSG00000156990', 'ENSG00000200034'], dtype=object)

In [ ]:
chrom = str(annotation_df.loc[feature_id,'chromosome'])
print(chrom)
start = annotation_df.loc[feature_id,'start']
print(start)
end = annotation_df.loc[feature_id,'end']
print(end)

#make robust to features specified back-to-front
lowest = min([start,end])
highest = max([start,end])

if (cis_mode) : 
    snpQuery = bim.query("chrom == '%s' & pos > %d & pos < %d" % (chrom, lowest-window_size, highest+window_size))
else :
    snpQuery = bim.query("(chrom == '%s' & (pos < %d | pos > %d))|chrom != '%s'" % (chrom, lowest-window_size, highest+window_size,chrom))
    snpQuery = snpQuery.loc[snpQuery['chrom'].map(lambda x: x in list(map(str, range(1, 23))))]
    
blocksize = 500

print(len(snpQuery))
if len(snpQuery) != 0:

    print(len(snpQuery)%blocksize)
    previous =0
    results_df = pd.DataFrame()
    print(results_df.shape)
    for snpGroup in chunker(snpQuery, blocksize):
        #Here we need to batch for cis & trans.
        snp_idxs = snpGroup['i'].values
        snp_names = snpGroup['snp'].values

        tested_snp_idxs.extend(snp_idxs)

        ##Check for NA's in feature. Remove samples with NA's

        sample_ids = individual2sample_df.loc[:,'sample'].values

        phenotype_ds = phenotype_df.loc[feature_id,sample_ids]
        contains_missing_samples = any(phenotype_ds.isnull().values)
        phenotype_ds.dropna(inplace=True)

        #indices for relevant individuals in genotype matrix    
        individual_ids = list(set(fam.index)&set(sample2individual_df.loc[phenotype_ds.index,'iid']))
        individual_idxs = fam.loc[individual_ids,'i'].values

        #subset genotype matrix, we cannot subselect at the same time, do in two steps.
        snp_df = pd.DataFrame(data=bed[snp_idxs,:].compute().transpose(),index=fam.index,columns=snp_names)
        snp_df = snp_df.loc[individual_ids,:]
        print(snp_df.shape)

In [ ]:
pass_qc_snps_all = []
fail_qc_snps_all = []
print(snp_df.shape)
print(contains_missing_samples)

#For the updated QC where we only use one individual per genotype. We can just select sites from df to test.
if not contains_missing_samples:
    #remove snps from snp_df if they fail QC
    snp_df = snp_df.loc[:,snp_df.columns[~snp_df.columns.isin(fail_qc_snps_all)]]
    snps_to_test_df = snp_df.loc[:,snp_df.columns[~snp_df.columns.isin(pass_qc_snps_all)]]
    
    #Only do QC on relevant SNPs. join pre-QCed list and new QCed list.
    #passed_snp_names,failed_snp_names = snp_qc.do_snp_qc(snps_to_test_df)
    #File will be called snp_qc.py
    passed_snp_names,failed_snp_names = do_snp_qc(snps_to_test_df, min_call_rate, min_maf, min_hwe_P)
    snps_to_test_df = None
    
    #append snp_names and failed_snp_names
    pass_qc_snps_all.extend(passed_snp_names)
    fail_qc_snps_all.extend(failed_snp_names)
    
    snp_names  = list(snp_df.columns[snp_df.columns.isin(pass_qc_snps_all)])
    #snp_names = ['snp_1_2739933', 'snp_1_2750437', 'snp_1_2752719', 'snp_1_2753372']
    snp_df = snp_df.loc[:,snp_df.columns[snp_df.columns.isin(pass_qc_snps_all)]]

else:
    #Do snp QC for relevant section.
    passed_snp_names,failed_snp_names = do_snp_qc(snp_df, min_call_rate, min_maf, min_hwe_P)
    snp_df = snp_df.loc[:,snp_df.columns[snp_df.columns.isin(pass_qc_snps_all)]]
    
    
# if len(snp_df.columns) != 0:
#     continue

snp_matrix = snp_df.values
snp_df = None

snp_matrix = Imputer(missing_values=np.nan,strategy='mean',axis=0,copy=False).fit_transform(snp_matrix)

if kinship_df is not None:
    kinship_mat = kinship_df.loc[individual_ids,individual_ids].values
else:
    kinship_mat = None

#map individual_ids to samples
sample_ids = individual2sample_df.loc[individual_ids,'sample'].values
phenotype = phenotype_ds.loc[sample_ids].values

#generate covariate matrix
if covariate_df is not None:
    cov_matrix = np.concatenate([np.ones((len(sample_ids),1)),covariate_df.loc[sample_ids,:].values],axis=1)
else:
    cov_matrix = None

#fit modelrun
LMM = limix.qtl.qtl_test_lmm(snp_matrix, phenotype,K=kinship_mat,covs=cov_matrix)


if(n_perm!=0):
    countPermutations = np.zeros((snp_matrix.shape[1]), dtype=np.int)
    nBetterCorrelation = np.zeros((snp_matrix.shape[1]), dtype=np.int)
    for permC in range(0,n_perm) :
        LMM_perm = limix.qtl.qtl_test_lmm(snp_matrix, np.random.permutation(phenotype),K=kinship_mat,covs=cov_matrix)
        #print(np.random.permutation(phenotype))
        for snp in range(0,len(LMM_perm.getPv()[0])):
            print(LMM_perm.getPv()[0][snp])
            print(LMM.getPv()[0][snp])
            if(LMM_perm.getPv()[0][snp]<=LMM.getPv()[0][snp]):
                nBetterCorrelation[snp]+=1
            else:
                print(LMM_perm.getPv()[0][snp])
                print(LMM.getPv()[0][snp])
            countPermutations[snp]+=1
    #Here we need to take care of the permutation data/
    #Relink phenotype to genotype (several options)
    #Drop using speed ups from fastQTL.
    #Calculate P-value using beta dist.


print(countPermutations)
print(nBetterCorrelation)
    
#add these results to qtl_results

temp_df = pd.DataFrame(index = range(len(snp_names)),columns=['feature_id','snp_id','p_value','beta','n_samples'])
temp_df['snp_id'] = snp_names
temp_df['feature_id'] = feature_id
temp_df['beta'] = LMM.getBetaSNP()[0]
temp_df['p_value'] = LMM.getPv()[0]
temp_df['n_samples'] = sum(~np.isnan(phenotype))
results_df = results_df.append(temp_df)
print(temp_df)
# output_writer.add_result_df(temp_df)

(90, 151)
False
0.247540836512
0.247540836512
0.561975176761
0.561975176761
0.561975176761
0.561975176761
0.77567287731
0.77567287731
0.894101600038
0.894101600038
0.557266427656
0.557266427656
0.894101600038
0.894101600038
0.697416082074
0.697416082074
0.557266427656
0.557266427656
0.894101600038
0.894101600038
0.965389529418
0.965389529418
0.369972393659
0.369972393659
0.764660271177
0.764660271177
0.647313766509
0.647313766509
0.647313766509
0.647313766509
0.931768964321
0.931768964321
0.142600980386
0.142600980386
0.0155108037191
0.0155108037191
0.292634252308
0.292634252308
0.19526673256
0.19526673256
0.263162083451
0.263162083451
0.572070984822
0.572070984822
0.39362297082
0.39362297082
0.534729693768
0.534729693768
0.299906108521
0.299906108521
0.447720211441
0.447720211441
0.256843322194
0.256843322194
0.0558123923274
0.0558123923274
0.689273620484
0.689273620484
0.0558123923274
0.0558123923274
0.888121053249
0.888121053249
0.971932148689
0.971932148689
0.971932148689
0.9719321

In [13]:
results_df = results_df.append(temp_df)
print(results_df)
results_df.empty

         feature_id         snp_id   p_value      beta  n_samples
0   ENSG00000215014  snp_1_1276077  0.933442  0.009569         90
1   ENSG00000215014  snp_1_1287922  0.027078 -0.523502         90
2   ENSG00000215014  snp_1_1299633  0.326317  0.206344         90
3   ENSG00000215014  snp_1_1308387  0.326317  0.206344         90
4   ENSG00000215014  snp_1_1469782  0.135740 -0.371984         90
5   ENSG00000215014  snp_1_1526799  0.198926  0.215296         90
6   ENSG00000215014  snp_1_1527952  0.087492  0.210162         90
7   ENSG00000215014  snp_1_1535700  0.357051  0.118735         90
8   ENSG00000215014  snp_1_1545289  0.215915  0.160522         90
9   ENSG00000215014  snp_1_1562536  0.420513 -0.140472         90
10  ENSG00000215014  snp_1_1584102  0.826237  0.025858         90
11  ENSG00000215014  snp_1_1590681  0.936862  0.009429         90
12  ENSG00000215014  snp_1_1602536  0.835972 -0.025113         90
13  ENSG00000215014  snp_1_1615348  0.871757 -0.019827         90
14  ENSG00

False

In [ ]:
# #     	/**
# 	 *
# 	 * @param probs
# 	 * @param variantAlleles the two alleles for this variant
# 	 * @param minProbability to call a genotype
# 	 * @return
# 	 */
# 	public static List<Alleles> convertProbabilitiesToAlleles(float[][] probs, Alleles variantAlleles, double minProbability) {

# 		ArrayList<Alleles> sampleAlleles = new ArrayList<Alleles>(probs.length);

# 		final int alleleCount = variantAlleles.getAlleleCount();

# 		if (alleleCount > 2 || alleleCount == 0) {
# 			throw new GenotypeDataException("Error converting posterior probabilities to called alleles. Found non biallelic SNP");
# 		}

# 		Alleles aa = Alleles.createAlleles(variantAlleles.get(0), variantAlleles.get(0));
# 		Alleles bb;

# 		if (alleleCount == 2) {
# 			bb = Alleles.createAlleles(variantAlleles.get(1), variantAlleles.get(1));
# 		} else {
# 			bb = null;
# 		}

# 		Alleles missing = Alleles.createAlleles(Allele.ZERO, Allele.ZERO);

# 		for (float[] sampleProbs : probs) {

# 			int maxProbIndex = -1;
# 			float maxProb = 0;

# 			int i = 0;
# 			for (float prob : sampleProbs) {
# 				if (prob > 0 && prob >= minProbability && prob > maxProb) {
# 					maxProbIndex = i;
# 					maxProb = prob;
# 				}
# 				++i;
# 			}

# 			if (alleleCount == 1 && maxProbIndex >= 1) {
# 				throw new GenotypeDataException("Error converting posterior probabilities to called alleles. Illigale probability.");
# 			}

# 			switch (maxProbIndex) {
# 				case -1:
# 					sampleAlleles.add(missing);
# 					break;
# 				case 0:
# 					sampleAlleles.add(aa);
# 					break;
# 				case 1:
# 					sampleAlleles.add(variantAlleles);
# 					break;
# 				case 2:
# 					sampleAlleles.add(bb);
# 					break;
# 				default:
# 					throw new GenotypeDataException("Error converting posterior probabilities to called alleles. This should not happen, please report this bug.");
# 			}

# 		}

# 		return sampleAlleles;

# 	}

# 	public static float[] convertProbabilitiesToDosage(float[][] probs, double minProbability) {

# 		float[] dosages = new float[probs.length];

# 		for (int i = 0; i < probs.length; ++i) {

# 			boolean containsMinProbability = false;

# 			for (float prob : probs[i]) {
# 				if (prob >= minProbability) {
# 					containsMinProbability = true;
# 					break;
# 				}
# 			}

# 			if (containsMinProbability) {

# 				dosages[i] = (probs[i][0] * 2) + probs[i][1];
# 				if (dosages[i] > 2) {
# 					dosages[i] = 2;
# 				}

# 			} else {
# 				dosages[i] = -1;
# 			}
# 		}

# 		return dosages;


# 	}